# COGS 108 - Data Wrangling

# Names

- Jiay Zhao
- Wenbo Hu
- Xiaotong Zeng
- Yunyi Huang

<a id='research_question'></a>
# Research Question

Is there a statistically significant relationship between the scale (burning area) of wildfire and  climate variables in California that are associated with global warming such as relative humidity level, temperature and wind speed? Additionally, how can we utilize these variables to predict the next wildfire event in California and the scale of wildfire?

# Dataset(s)

**Dataset Name:** California Wildfire Incidents (2013-2020) --- List of wildfires in California between 2013 and 2020<br>
**Link to the dataset:** https://www.kaggle.com/ananthu017/california-wildfire-incidents-20132020 <br>
**Number of observations:** 1636 x 40 = 65440<br>
**Description of the dataset:** This dataset contains the list of wildfires that have occurred in California between 2013 and 2020, and it also includes other variables such as location and injuries. 


**Dataset Name:** NOAA Daily global surface summary 2013-2019<br>
**Link to the dataset:** https://www.ncei.noaa.gov/data/global-summary-of-the-day/archive/ <br>
**Number of observations:** We are going to use the sub datasets of the year 2013-2019, as well as the dataset for stations. The number of observations for each datasets are below:
- 2013: 4.01m
- 2014: 4.12m
- 2015: 4.20m
- 2016: 4.29m
- 2017: 4.29m
- 2018: 4.01m
- 2019: 3.29m
<br>

**Description of the dataset:** These datasets contain the weather records, including temperature, precipitation, and wind speed, etc., of different weather stations around the world. There is no direct information of humidity from this dataset, so we get the temperature and dew point to calculate the relative humidity percentage.



**Dataset Name:** The Integrated Surface Data (ISD) Station List<br>
**Link to the dataset:**  https://www1.ncdc.noaa.gov/pub/data/noaa/isd-history.csv <br>
**Number of observations:** 29700 <br>
**Description of the dataset:** This dataset contains identification numbers and information for weather stations in the Federal Climate Complex ISD.

**Data Combination:** In order to perform our analysis on these dataset, we firstly clean and wrangle each dataset separately. For the second dataset, which is the NOAA GSOD Daily global surface summary, we will need to combine the sub datasets together since the datasets were divided into different years. After we finished cleaning each dataset, we will merge them together by weather station id and date of the event.

# Setup

In [2]:
## YOUR CODE HERE
# Import pandas to read csv file and manage heterogenous data
import pandas as pd

# Import numpy to store numeric information and perform numerical analysis
import numpy as np

# Import seaborn and matplotlib to visualize data
import seaborn as sns
import matplotlib.pyplot as plt

import shutil

import os

In [3]:
for dirname, _, filenames in os.walk('/Users/wenbohu/Desktop/Weather'):
    for filename in filenames:
        print((os.path.join(dirname, filename)))

/Users/wenbohu/Desktop/Weather/.DS_Store
/Users/wenbohu/Desktop/Weather/2013/57328099999.csv
/Users/wenbohu/Desktop/Weather/2013/71393099999.csv
/Users/wenbohu/Desktop/Weather/2013/02602099999.csv
/Users/wenbohu/Desktop/Weather/2013/72210103039.csv
/Users/wenbohu/Desktop/Weather/2013/71670099999.csv
/Users/wenbohu/Desktop/Weather/2013/95658099999.csv
/Users/wenbohu/Desktop/Weather/2013/68377099999.csv
/Users/wenbohu/Desktop/Weather/2013/89266099999.csv
/Users/wenbohu/Desktop/Weather/2013/72548404942.csv
/Users/wenbohu/Desktop/Weather/2013/71446099999.csv
/Users/wenbohu/Desktop/Weather/2013/72784094187.csv
/Users/wenbohu/Desktop/Weather/2013/47823099999.csv
/Users/wenbohu/Desktop/Weather/2013/95975099999.csv
/Users/wenbohu/Desktop/Weather/2013/38880099999.csv
/Users/wenbohu/Desktop/Weather/2013/72511704827.csv
/Users/wenbohu/Desktop/Weather/2013/72211454901.csv
/Users/wenbohu/Desktop/Weather/2013/89050099999.csv
/Users/wenbohu/Desktop/Weather/2013/72203163839.csv
/Users/wenbohu/Desktop/

In [4]:
# get all subdiretory of all tables
file_dict ={}
for path, dirs, files in os.walk('/Users/wenbohu/Desktop/Weather', topdown=False):
    file_dict[path]=files

In [5]:
file_dict

{'/Users/wenbohu/Desktop/Weather/2013': ['57328099999.csv',
  '71393099999.csv',
  '02602099999.csv',
  '72210103039.csv',
  '71670099999.csv',
  '95658099999.csv',
  '68377099999.csv',
  '89266099999.csv',
  '72548404942.csv',
  '71446099999.csv',
  '72784094187.csv',
  '47823099999.csv',
  '95975099999.csv',
  '38880099999.csv',
  '72511704827.csv',
  '72211454901.csv',
  '89050099999.csv',
  '72203163839.csv',
  '07027099999.csv',
  '74206024207.csv',
  '68188099999.csv',
  '47681099999.csv',
  '47648099999.csv',
  '72747704970.csv',
  '91186022534.csv',
  '72537614853.csv',
  '71736099999.csv',
  '02744099999.csv',
  '17292099999.csv',
  '02869099999.csv',
  '07482099999.csv',
  '42895099999.csv',
  '47154099999.csv',
  '72598524267.csv',
  '40859099999.csv',
  '95833099999.csv',
  '72367723054.csv',
  '17547099999.csv',
  '71500099999.csv',
  '01092099999.csv',
  '48465099999.csv',
  '72272803196.csv',
  '72421093814.csv',
  '06484099999.csv',
  '14544099999.csv',
  '16541099999.c

In [6]:
paths = list(file_dict.keys())

In [7]:
events = []
for path in paths:
    events += [os.path.join(path,file) for file in file_dict[path]]

# Data Cleaning

Since we have three data set, we choose to clean them seperatly and then merge these dataset by locations.

#### **First**, we upload the California wildfire incidents data set

Have a brief look of the data and Scrap the data

In [8]:
# Load the California wildfire incidents data set in data frame
# We get this data set from Kaggle (https://www.kaggle.com/ananthu017/california-wildfire-incidents-20132020)
wildfire = pd.read_csv("California_Fire_Incidents.csv")

In [9]:
print('The California fire incidents data set shape is ', wildfire.shape)
wildfire.head()

The California fire incidents data set shape is  (1636, 40)


AcresBurned  Active                                          AdminUnit  \
0     257314.0   False  Stanislaus National Forest/Yosemite National Park   
1      30274.0   False  USFS Angeles National Forest/Los Angeles Count...   
2      27531.0   False  CAL FIRE Riverside Unit / San Bernardino Natio...   
3      27440.0   False                              Tahoe National Forest   
4      24251.0   False                       Ventura County Fire/CAL FIRE   

   AirTankers  ArchiveYear  CalFireIncident  \
0         NaN         2013             True   
1         NaN         2013             True   
2         NaN         2013             True   
3         NaN         2013            False   
4         NaN         2013             True   

                            CanonicalUrl  \
0         /incidents/2013/8/17/rim-fire/   
1  /incidents/2013/5/30/powerhouse-fire/   
2    /incidents/2013/7/15/mountain-fire/   
3    /incidents/2013/8/10/american-fire/   
4      /incidents/2013/5/2/springs-fire/   

                                  ConditionStatement ControlStatement  \
0                                                NaN              NaN   
1                                                NaN              NaN   
2                                                NaN              NaN   
3                                                NaN              NaN   
4  Acreage has been reduced based upon more accur...              NaN   

      Counties  ...                                     SearchKeywords  \
0     Tuolumne  ...  Rim Fire, Stanislaus National Forest, Yosemite...   
1  Los Angeles  ...  Powerhouse Fire, May 2013, June 2013, Angeles ...   
2    Riverside  ...  Mountain Fire, July 2013, Highway 243, Highway...   
3       Placer  ...  American Fire, August 2013, Deadwood Ridge, Fo...   
4      Ventura  ...  Springs Fire, May 2013, Highway 101, Camarillo...   

                Started     Status  StructuresDamaged StructuresDestroyed  \
0  2013-08-17T15:25:00Z  Finalized                NaN                 NaN   
1  2013-05-30T15:28:00Z  Finalized                NaN                 NaN   
2  2013-07-15T13:43:00Z  Finalized                NaN                 NaN   
3  2013-08-10T16:30:00Z  Finalized                NaN                 NaN   
4  2013-05-02T07:01:00Z  Finalized                6.0                10.0   

   StructuresEvacuated  StructuresThreatened  \
0                  NaN                   NaN   
1                  NaN                   NaN   
2                  NaN                   NaN   
3                  NaN                   NaN   
4                  NaN                   NaN   

                               UniqueId               Updated  WaterTenders  
0  5fb18d4d-213f-4d83-a179-daaf11939e78  2013-09-06T18:30:00Z           NaN  
1  bf37805e-1cc2-4208-9972-753e47874c87  2013-06-08T18:30:00Z           NaN  
2  a3149fec-4d48-427c-8b2c-59e8b79d59db  2013-07-30T18:00:00Z           NaN  
3  8213f5c7-34fa-403b-a4bc-da2ace6e6625  2013-08-30T08:00:00Z           NaN  
4  46731fb8-3350-4920-bdf7-910ac0eb715c  2013-05-11T06:30:00Z          11.0  

[5 rows x 40 columns]

Since we only need the dates, acres burned (scale), and county name for the following analysis, we update these information back to 'fire'.

In [10]:
# delete the irrelevant columns
wildfire = wildfire[['AcresBurned','Started','Counties', 'Latitude', 'Longitude']]

# change the started time into date
#wildfire['Started'] = pd.to_datetime(wildfire['Started'])
wildfire['Started'] = [x[0:10] for x in wildfire['Started']]

# change the 'Started' column name into 'Date'
wildfire = wildfire.rename({'Started':'Date'}, axis='columns')

#drop the null values 
wildfire['Latitude'] = wildfire['Latitude'].apply(lambda x: np.nan if x == 0 else x)
wildfire = wildfire.dropna().reset_index(drop=True) 
wildfire.head()

AcresBurned        Date     Counties   Latitude   Longitude
0     257314.0  2013-08-17     Tuolumne  37.857000 -120.086000
1      30274.0  2013-05-30  Los Angeles  34.585595 -118.423176
2      27531.0  2013-07-15    Riverside  33.709500 -116.728850
3      27440.0  2013-08-10       Placer  39.120000 -120.650000
4      22992.0  2013-07-22       Fresno  37.279000 -119.318000

#### Second, upload the Integrated Surface Data (ISD) station list

Clean the station table

In [11]:
# Load the US weather data set in data frame
# We get the Integrated Surface Data (ISD) station list from ncdc.noaa.gov
station = pd.read_csv("isd-history.csv") 

# Since the weather station ID is a combination of column 'USAF' and 'WBAN',
# we combine these two columns into a new column called 'ID'
station['ID']= station['USAF'].astype(str) + station['WBAN'].astype(str)

# we only analyze California weather
station = station[(station['STATE']=='CA') & (station['CTRY']=='US')].reset_index(drop=True) 

# station only need to include the ID and the nameof the station
# station = station[['ID','STATION NAME']]
pd.set_option("max_rows", None)
station

USAF   WBAN                                 STATION NAME CTRY STATE  \
0    690020  93218                 JOLON HUNTER LIGGETT MIL RES   US    CA   
1    690020  99999                 JOLON HUNTER LIGGETT MIL RES   US    CA   
2    690070  93217                                FRITZSCHE AAF   US    CA   
3    690140  93101                                 EL TORO MCAS   US    CA   
4    690150  93121                            TWENTY NINE PALMS   US    CA   
5    690150  99999                             TWENTYNINE PALMS   US    CA   
6    690584  99999                           LZ BULL / EXERCISE   US    CA   
7    691224  99999                                AFWA ASSIGNED   US    CA   
8    691414  99999                           SPEED BAG AIRFIELD   US    CA   
9    692494  99999                          SUPERIOR VALLEY G R   US    CA   
10   692694  99999                         FOB MIAMI NTC/EXERCI   US    CA   
11   693654  99999                                   NTC MOBILE   US    CA   
12   695414  99999                          RED PASS LAKE / NTC   US    CA   
13   695424  99999                                AFWA ASSIGNED   US    CA   
14   697534  99999                                   FORT IRWIN   US    CA   
15   698114  99999                              METMFR 29 PALMS   US    CA   
16   720046  99999                                      NEWHALL   US    CA   
17   720165  99999                    WARNER SPRINGS GLIDERPORT   US    CA   
18   720193    117        LONNIE POOL FIELD WEAVERVILLE AIRPORT   US    CA   
19   720267  23224                     AUBURN MUNICIPAL AIRPORT   US    CA   
20   720267  99999                             AUBURN MUNICIPAL   US    CA   
21   720329  99999                                        CABLE   US    CA   
22   720333  53175                     CORONA MUNICIPAL AIRPORT   US    CA   
23   720333  99999                                  CORONA MUNI   US    CA   
24   720406    135                          GNOSS FIELD AIRPORT   US    CA   
25   720406  99999                          GNOSS FIELD AIRPORT   US    CA   
26   720576    174                           UNIVERSITY AIRPORT   US    CA   
27   720576  99999                                        DAVIS   US    CA   
28   720614    205   LINCOLN REGIONAL AIRPORT KARL HARDER FIELD   US    CA   
29   720615    206                             COLUMBIA AIRPORT   US    CA   
30   720645    227                          PLACERVILLE AIRPORT   US    CA   
31   720646    228                        HALF MOON BAY AIRPORT   US    CA   
32   720652    433                   BRIDGEPORT SONORA JUNCTION   US    CA   
33   720652  99999             USMC MTN WARFARE TRAINING CENTER   US    CA   
34   720681  99999             CALAVERAS CO MAURY RASMUSSEN FLD   US    CA   
35   720687  99999                                   HEMET RYAN   US    CA   
36   720935  99999                                PETALUMA MUNI   US    CA   
37   720952  99999                               GRAY BUTTE FLD   US    CA   
38   721027  99999                               TRINITY CENTER   US    CA   
39   722810  23199                                          NAF   US    CA   
40   722859  99999                                   DANA POINT   US    CA   
41   722860  23119                       MARCH AIR RESERVE BASE   US    CA   
42   722860  99999                          RIVERSIDE/MARCH AFB   US    CA   
43   722864  99999                           BIG BEAR CITY ARPT   US    CA   
44   722865  93180                                      ONTARIO   US    CA   
45   722865  99999                                      ONTARIO   US    CA   
46   722866  23122         SAN BERNARDINO INTERNATIONAL AIRPORT   US    CA   
47   722866  99999                          SAN BERNARDINO INTL   US    CA   
48   722867  23156                                     BEAUMONT   US    CA   
49   722867  99999                                     BEAUMONT   US    CA   
50   722868  93138           

In [7]:
station.dtypes

USAF             object
WBAN              int64
STATION NAME     object
CTRY             object
STATE            object
ICAO             object
LAT             float64
LON             float64
ELEV(M)         float64
BEGIN             int64
END               int64
ID               object
dtype: object

In [8]:
IDlist = []
for i,j in wildfire.iterrows():
    before = len(IDlist)
    for a,b in station.iterrows():
        #about 50km * 40km (just for first time test then tried 0.3, 0.1, and 0.2)
        if (((b['LAT'] <= j['Latitude'] + 0.2) and (b['LAT'] >= j['Latitude'] - 0.2)) 
        and (( b['LON'] <= j['Longitude'] + 0.2) and ( b['LON'] >= j['Longitude'] - 0.2))):
            IDlist.append(b['ID'])
            break
    after = len(IDlist)
    if (before == after):
        IDlist.append("Not_Found")
           

In [9]:
IDlist

['Not_Found',
 '99999923180',
 'Not_Found',
 '72584523225',
 'Not_Found',
 '72068799999',
 'Not_Found',
 'Not_Found',
 'Not_Found',
 '9999994222',
 '99999923178',
 'Not_Found',
 'Not_Found',
 'Not_Found',
 'Not_Found',
 '72016599999',
 '72493623254',
 'Not_Found',
 'Not_Found',
 '72292399999',
 'Not_Found',
 '72392399999',
 '99999953150',
 'Not_Found',
 '99999923178',
 'Not_Found',
 'Not_Found',
 '72383023187',
 '72004699999',
 'Not_Found',
 'Not_Found',
 '72016599999',
 'Not_Found',
 '72068799999',
 'Not_Found',
 'Not_Found',
 '72493623254',
 'Not_Found',
 '72032999999',
 'Not_Found',
 'Not_Found',
 '99999993243',
 '74504893210',
 'Not_Found',
 '74504893210',
 '72497099999',
 'Not_Found',
 '7228873180',
 'Not_Found',
 'Not_Found',
 '72492723285',
 '720614205',
 'Not_Found',
 '72286623122',
 '72591024216',
 'Not_Found',
 '72591024216',
 '72495593227',
 '72293599999',
 'Not_Found',
 'Not_Found',
 'Not_Found',
 '720406135',
 '720406135',
 '72286023119',
 '72492523240',
 'Not_Found',
 '72

In [10]:
len(IDlist)

1479

In [11]:
# find which diameter we should choose for more unique stations
# 0.5-95 0.3-119 0.1-119 0.2-127(THIS IS THE BEST!!!!)
# when 0.1 it's also 119 but lots of not found values
unique = []
for x in IDlist:
    if x not in unique:
        unique.append(x)
print(len(unique))

127


In [17]:
# get dataframe
IDlist = []
row_fire = []
join_id =[]
num = 1
matched_wildfire = pd.DataFrame(columns=wildfire.columns)
for i,j in wildfire.iterrows():
    for a,b in station.iterrows():
        #about 22.2km * 20km (we also tried 0.3, 0.1, and 0.2)
        if (((b['LAT'] <= j['Latitude'] + 0.2) and (b['LAT'] >= j['Latitude'] - 0.2)) 
        and (( b['LON'] <= j['Longitude'] + 0.2) and ( b['LON'] >= j['Longitude'] - 0.2))):
            IDlist.append(b['ID'])
            join_id.append(num)
            num += 1
            row_fire.append(list(j))
            break
            
matched_wildfire = matched_wildfire.append(pd.DataFrame(row_fire,columns=wildfire.columns))
matched_wildfire = matched_wildfire.assign(Station_ID = IDlist)
matched_wildfire = matched_wildfire.assign(Join_ID=join_id)

matched_wildfire

AcresBurned        Date         Counties   Latitude   Longitude  \
0        30274.0  2013-05-30      Los Angeles  34.585595 -118.423176   
1        27440.0  2013-08-10           Placer  39.120000 -120.650000   
2        20292.0  2013-08-07        Riverside  33.861570 -116.904270   
3         8073.0  2013-09-09           Shasta  40.498332 -122.535496   
4         7055.0  2013-07-06        San Diego  32.954350 -116.473810   
5         3166.0  2013-05-01        Riverside  34.288877 -116.941311   
6         3111.0  2013-09-08     Contra Costa  37.907570 -121.882582   
7         2236.0  2013-10-05        San Diego  33.341000 -117.309200   
8         1984.0  2013-05-27    Santa Barbara  34.550480 -119.824290   
9         1708.0  2013-06-16         Mariposa  37.582020 -119.910710   
10        1271.0  2013-05-26        San Diego  33.044580 -116.520900   
11         712.0  2013-07-19             Kern  34.882000 -118.919400   
12         712.0  2013-05-17      Los Angeles  34.491490 -118.610044   
13         534.0  2013-06-28   San Bernardino  34.071556 -117.048397   
14         510.0  2013-05-04        Riverside  33.894055 -116.855019   
15         492.0  2013-07-01     Contra Costa  37.968660 -121.914530   
16         413.0  2013-08-20   San Bernardino  34.302000 -117.598000   
17         354.0  2013-05-03       San Benito  37.160346 -120.937494   
18         305.0  2013-10-04            Butte  39.439000 -121.497000   
19         298.0  2013-06-03            Butte  39.434183 -121.576804   
20         274.0  2013-07-01     Contra Costa  39.904650 -121.743670   
21         268.0  2013-09-23      Los Angeles  34.149000 -117.908000   
22         240.0  2013-06-08          Alameda  37.775057 -121.737213   
23         237.0  2013-06-13           Placer  38.729297 -121.380862   
24         200.0  2013-09-24   San Bernardino  34.200000 -117.417000   
25         200.0  2013-07-04           Tehama  40.012398 -122.079871   
26         195.0  2013-07-19           Tehama  39.961309 -122.330879   
27         190.0  2013-11-21             Napa  38.382000 -122.311000   
28         170.0  2013-05-28    Santa Barbara  34.611824 -120.074655   
29         159.0  2013-10-04           Sonoma  38.345990 -122.650300   
30         158.0  2013-07-26           Sonoma  38.176930 -122.512530   
31         150.0  2013-07-16        Riverside  33.990128 -117.164997   
32         150.0  2013-07-12       Stanislaus  37.436000 -121.195500   
33         149.0  2013-05-28      Los Angeles  34.419284 -118.586880   
34         125.0  2013-05-01           Sonoma  38.638828 -122.655616   
35         124.0  2013-06-18           Solano  38.087440 -122.138020   
36         124.0  2013-05-25        Riverside  33.963591 -117.187934   
37         116.0  2013-08-16        El Dorado  38.682378 -120.839075   
38         108.0  2013-06-13           Fresno  36.772425 -119.628389   
39         100.0  2013-06-02         Tuolumne  37.915290 -120.333130   
40         100.0  2013-05-22        San Diego  32.564465 -116.900368   
41          94.0  2013-09-24  San Luis Obispo  35.439300 -120.835800   
42          92.0  2013-08-01            Butte  39.661200 -121.503540   
43          90.0  2013-05-21        Riverside  33.958200 -116.653400   
44          82.0  2013-11-22        Mendocino  39.044200 -123.147800   
45          80.0  2013-08-31            Butte  39.731878 -121.713938   
46          75.0  2013-05-13   San Bernardino  34.183400 -117.440800   
47          73.0  2013-09-11   San Bernardino  34.003151 -117.106075   
48          73.0  2013-07-08             Yuba  39.206000 -121.316340   
49          64.0  2013-11-14          Ventura  34.384000 -119.132490   
50          60.0  2013-08-04        Riverside  33.910270 -116.998950   
51          52.0  2013-08-31           Nevada  39.333401 -121.107022   
52          51.0  2013-11-08  San Luis Obispo  35.457978 -120.751555   
53          50.0  2013-08-15         Siskiyou  41.923323 -122.578393   
54          50.0  2013-07-12      Santa Clara

In [40]:
matched_wildfire.shape

(842, 6)

#### Third, using 'wildfire' and 'station' to form a data frame of the weather data in CA from 2013 to 2019

In [ ]:
# We get the weather data from (https://www.ncei.noaa.gov/data/global-summary-of-the-day/archive/)
# We only need the weather data from 2013 to 2019 with the ID contained in 'station'

In [14]:
example = pd.read_csv("/Users/wenbohu/Desktop/Weather/2013/40854099999.csv")
example

STATION        DATE   LATITUDE  LONGITUDE  ELEVATION     NAME   TEMP  \
0    40854099999  2013-01-01  29.083925  58.450397      940.0  BAM, IR   44.1   
1    40854099999  2013-01-02  29.083925  58.450397      940.0  BAM, IR   43.4   
2    40854099999  2013-01-03  29.083925  58.450397      940.0  BAM, IR   43.9   
3    40854099999  2013-01-04  29.083925  58.450397      940.0  BAM, IR   44.4   
4    40854099999  2013-01-05  29.083925  58.450397      940.0  BAM, IR   45.2   
5    40854099999  2013-01-06  29.083925  58.450397      940.0  BAM, IR   51.8   
6    40854099999  2013-01-07  29.083925  58.450397      940.0  BAM, IR   59.2   
7    40854099999  2013-01-08  29.083925  58.450397      940.0  BAM, IR   65.3   
8    40854099999  2013-01-09  29.083925  58.450397      940.0  BAM, IR   64.0   
9    40854099999  2013-01-10  29.083925  58.450397      940.0  BAM, IR   66.1   
10   40854099999  2013-01-11  29.083925  58.450397      940.0  BAM, IR   61.4   
11   40854099999  2013-01-12  29.083925  58.450397      940.0  BAM, IR   42.0   
12   40854099999  2013-01-13  29.083925  58.450397      940.0  BAM, IR   41.1   
13   40854099999  2013-01-14  29.083925  58.450397      940.0  BAM, IR   42.4   
14   40854099999  2013-01-15  29.083925  58.450397      940.0  BAM, IR   42.7   
15   40854099999  2013-01-16  29.083925  58.450397      940.0  BAM, IR   41.1   
16   40854099999  2013-01-17  29.083925  58.450397      940.0  BAM, IR   40.2   
17   40854099999  2013-01-18  29.083925  58.450397      940.0  BAM, IR   44.7   
18   40854099999  2013-01-19  29.083925  58.450397      940.0  BAM, IR   49.6   
19   40854099999  2013-01-20  29.083925  58.450397      940.0  BAM, IR   53.9   
20   40854099999  2013-01-21  29.083925  58.450397      940.0  BAM, IR   59.1   
21   40854099999  2013-01-22  29.083925  58.450397      940.0  BAM, IR   57.5   
22   40854099999  2013-01-23  29.083925  58.450397      940.0  BAM, IR   55.9   
23   40854099999  2013-01-24  29.083925  58.450397      940.0  BAM, IR   58.9   
24   40854099999  2013-01-25  29.083925  58.450397      940.0  BAM, IR   60.9   
25   40854099999  2013-01-26  29.083925  58.450397      940.0  BAM, IR   63.1   
26   40854099999  2013-01-27  29.083925  58.450397      940.0  BAM, IR   62.0   
27   40854099999  2013-01-28  29.083925  58.450397      940.0  BAM, IR   61.6   
28   40854099999  2013-01-29  29.083925  58.450397      940.0  BAM, IR   66.0   
29   40854099999  2013-01-30  29.083925  58.450397      940.0  BAM, IR   66.4   
30   40854099999  2013-01-31  29.083925  58.450397      940.0  BAM, IR   65.2   
31   40854099999  2013-02-01  29.083925  58.450397      940.0  BAM, IR   66.9   
32   40854099999  2013-02-02  29.083925  58.450397      940.0  BAM, IR   62.4   
33   40854099999  2013-02-03  29.083925  58.450397      940.0  BAM, IR   52.6   
34   40854099999  2013-02-04  29.083925  58.450397      940.0  BAM, IR   47.7   
35   40854099999  2013-02-05  29.083925  58.450397      940.0  BAM, IR   49.7   
36   40854099999  2013-02-06  29.083925  58.450397      940.0  BAM, IR   57.4   
37   40854099999  2013-02-07  29.083925  58.450397      940.0  BAM, IR   61.4   
38   40854099999  2013-02-08  29.083925  58.450397      940.0  BAM, IR   64.3   
39   40854099999  2013-02-09  29.083925  58.450397      940.0  BAM, IR   59.6   
40   40854099999  2013-02-10  29.083925  58.450397      940.0  BAM, IR   58.7   
41   40854099999  2013-02-11  29.083925  58.450397      940.0  BAM, IR   60.8   
42   40854099999  2013-02-12  29.083925  58.450397      940.0  BAM, IR   63.1   
43   40854099999  2013-02-13  29.083925  58.450397      940.0  BAM, IR   60.2   
44   40854099999  2013-02-14  29.083925  58.450397      940.0  BAM, IR   54.4   
45   40854099999  2013-02-15  29.083925  58.450397      940.0  BAM, IR   51.6   
46   40854099999  2013-02-16  29.083925  58.450397      940.0  BAM, IR   56.7   
47   40854099999  2013-02-17  29.083925  58.450397      940.0  BAM, IR   65.6   
48   40854099999  2013-02-18  29.083925 

In [39]:
# Get the weather information of wildfire start date 
row_weather = []
join_id = []
num = 1
weather = pd.DataFrame(columns = example.columns)
for i, j in matched_wildfire.iterrows():
    for file in events:
        if num in join_id:
            break
        if (file[-15:-4] == j['Station_ID']):
            temp = pd.read_csv(file)
            for a, b in temp.iterrows():
                if (b["DATE"] == j['Date']):
                    row_weather.append(list(b))
                    join_id.append(num)
                    break 
    num += 1
                

In [53]:
weather = pd.DataFrame(columns = example.columns)
weather = weather.append(pd.DataFrame(row_weather, columns = example.columns))
weather = weather.assign(Join_ID = join_id)
weather

STATION        DATE   LATITUDE   LONGITUDE  ELEVATION  \
0    99999953150  2013-06-16  37.759200 -119.820800    2017.80   
1    72383023187  2013-07-19  34.743600 -118.724200    1374.60   
2    99999993243  2013-05-03  37.238100 -120.882500      23.80   
3    74504893210  2013-10-04  39.490000 -121.618330      57.90   
4    74504893210  2013-06-03  39.490000 -121.618330      57.90   
5    72492723285  2013-06-08  37.692700 -121.814400     119.80   
6    72591024216  2013-07-04  40.151900 -122.253600     107.60   
7    72591024216  2013-07-19  40.151900 -122.253600     107.60   
8    72495593227  2013-11-21  38.210200 -122.284700       4.30   
9    72286023119  2013-07-16  33.900000 -117.250000     468.20   
10   72495723213  2013-05-01  38.503800 -122.810200      34.70   
11   72286023119  2013-05-25  33.900000 -117.250000     468.20   
12   72389093193  2013-06-13  36.780000 -119.719400     101.50   
13   74504893210  2013-08-01  39.490000 -121.618330      57.90   
14   72286893138  2013-05-21  33.822200 -116.504300     124.70   
15   72590523275  2013-11-22  39.125830 -123.200830     183.20   
16   72286023119  2013-09-11  33.900000 -117.250000     468.20   
17   72483793216  2013-07-08  39.133330 -121.433330      38.10   
18   72595524259  2013-08-15  41.781390 -122.468060     808.00   
19   72494693232  2013-07-12  37.333330 -121.816670      40.50   
20   72396593209  2013-05-25  35.669700 -120.628300     246.90   
21   72590523275  2013-07-23  39.125830 -123.200830     183.20   
22   72286023119  2013-06-08  33.900000 -117.250000     468.20   
23   72494693232  2013-12-31  37.333330 -121.816670      40.50   
24   72286023119  2013-07-19  33.900000 -117.250000     468.20   
25   72286023119  2013-06-14  33.900000 -117.250000     468.20   
26   72492723285  2013-07-06  37.692700 -121.814400     119.80   
27   72389093193  2013-06-13  36.780000 -119.719400     101.50   
28   72016599999  2013-04-20  34.263619 -116.854475    2056.79   
29   72482893241  2013-06-10  38.377500 -121.957500      33.20   
30   72482893241  2013-06-10  38.377500 -121.957500      33.20   
31   72482893241  2013-06-10  38.377500 -121.957500      33.20   
32   72482893241  2013-06-10  38.377500 -121.957500      33.20   
33   72286023119  2013-07-19  33.900000 -117.250000     468.20   
34   72482893241  2014-07-04  38.377500 -121.957500      33.20   
35   72289523243  2014-05-13  34.666670 -120.466670      26.80   
36   72595724215  2014-09-15  41.332500 -122.332780    1077.50   
37   72026723224  2014-09-13  38.954720 -121.081940     466.60   
38   72591024216  2014-06-13  40.151900 -122.253600     107.60   
39   72480023157  2014-04-19  37.371100 -118.358000    1250.30   
40   72584693201  2014-08-18  39.320000 -120.139440    1798.30   
41   74504893210  2014-07-14  39.490000 -121.618330      57.90   
42   72483793216  2014-07-07  39.133330 -121.433330      38.10   
43   72584793230  2014-09-25  38.898300 -119.994700    1924.50   
44   72289793206  2015-08-16  35.237220 -120.641390      61.00   
45   72584523225  2015-07-25  39.277400 -120.710200    1608.10   
46   72033353175  2015-04-18  33.897650 -117.602430     162.50   
47   99999993243  2015-05-11  37.238100 -120.882500      23.80   
48   72095299999  2015-07-17  34.563889 -117.675000     920.49   
49   72492723285  2015-07-30  37.692700 -121.814400     119.80   
50   72595524259  2015-07-13  41.781390 -122.468060     808.00   
51   72290753143  2015-06-17  32.826110 -116.972500     118.00   
52   72483793216  2015-06-18  39.133330 -121.433330      38.10   
53   72482893241  2015-07-06  38.377500 -121.957500      33.20   
54   72394023273  2015-08-01  34.899400 -120.448600      73.80   
55   72026723224  2015-09-22  38.954720 -121.081940     466.60   
56   72026723224  2015-07-22  38.954720 -121.081940     466.60   
57   74505653120  2015-07-16  33.037500 -116.915830     424.60   
58   72590523275  2015-07-04  39.125830 -123.200830     183.20   
59   72033353175  2015-07-12  33.897650 -117.6024

In [54]:
dataframe = matched_wildfire.merge(weather, on = 'Join_ID')

In [55]:
dataframe.to_csv('/Users/wenbohu/Desktop/df.csv')